# now do some ML using the web scraped data

In [1544]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [1545]:
from player_data_expansion import get_all_expanded_player_fight_data

In [1546]:
# AWS integration getting file data
df_init = pd.read_csv("fight_data.csv").fillna(pd.NA)
df_init.head()

Date        fighter1 fighter1_result method_or_round  \
0    Sunday, 4 May 2025     Naoya Inoue          Winner    TKO, Round 8   
1  Saturday, 3 May 2025  Canelo Alvarez          Winner    UD, Round 12   
2  Saturday, 3 May 2025   Jukiya Iimura          Winner    UD, Round 12   
3    Friday, 2 May 2025     Ryan Garcia           Loser    UD, Round 12   
4  Thursday, 1 May 2025    Kevin Lerena          Winner    TKO, Round 3   

                 fighter2                                      Venue  \
0          Ramon Cardenas   T-Mobile Arena, Las Vegas, United States   
1           William Scull            The Venue, Riyadh, Saudi Arabia   
2          Esneth Domingo                Korakuen Hall, Tokyo, Japan   
3  Rolando ‘Rolly’ Romero  Times Square, New York, NY, United States   
4        Serhiy Radchenko       Sunbet Arena, Pretoria, South Africa   

                                    Undercard fights  \
0  Rafael Espinoza Beat  Edward Vazquez (TKO 7) \...   
1  Jaime Munguia Beat  Bruno Surace (UD 12) \nMar...   
2                                               <NA>   
3  Devin Haney Beat  Jose Ramirez (UD 12) \nTeofi...   
4                                               <NA>   

                                           link  fighter1_record_wins  \
0    https://box.live/fights/inoue-vs-cardenas/                    29   
1      https://box.live/fights/canelo-vs-scull/                    62   
2    https://box.live/fights/iimura-vs-domingo/                     8   
3     https://box.live/fights/garcia-vs-romero/                    24   
4  https://box.live/fights/lerena-vs-radchenko/                    30   

   fighter1_record_draws  fighter1_record_losses  fighter2_record_wins  \
0                      0                       0                    26   
1                      2                       2                    23   
2                      1                       0                    21   
3                      1                       0                    16   
4                      3                       0                    11   

   fighter2_record_draws  fighter2_record_losses  fighter1_height_cm  \
0                      1                       0                 164   
1                      0                       0                 175   
2                      2                       0                 164   
3                      2                       0                 178   
4                      7                       0                 185   

   fighter2_height_cm  fighter1_ko_percentage  fighter2_ko_percentage  
0               168.0                       0                       0  
1               182.0                       0                       0  
2               160.0                       0                       0  
3               173.0                      83                      81  
4               186.0                      47                      45

In [1547]:
# ADD BASIC DATA TO SEE IF IT WORKS
df_init = pd.concat([pd.read_csv("fight_data_backup_basic.csv"), df_init], axis=0)
df_init.drop_duplicates(inplace=True)

### start cleaning

In [1548]:
df_essentials = df_init.drop(columns=['link','Venue','Date','Undercard fights','fighter1','fighter2'])
df_essentials.head(2)

fighter1_result method_or_round  fighter1_record_wins  \
0          Winner    RTD, Round 3                   NaN   
1          Winner    UD, Round 12                   NaN   

   fighter1_record_draws  fighter1_record_losses  fighter2_record_wins  \
0                    NaN                     NaN                   NaN   
1                    NaN                     NaN                   NaN   

   fighter2_record_draws  fighter2_record_losses  fighter1_height_cm  \
0                    NaN                     NaN                 NaN   
1                    NaN                     NaN                 NaN   

   fighter2_height_cm  fighter1_ko_percentage  fighter2_ko_percentage  
0                 NaN                     NaN                     NaN  
1                 NaN                     NaN                     NaN

In [1549]:
df_staged_cleaning = df_essentials.copy()
df_staged_cleaning.head(2)

fighter1_result method_or_round  fighter1_record_wins  \
0          Winner    RTD, Round 3                   NaN   
1          Winner    UD, Round 12                   NaN   

   fighter1_record_draws  fighter1_record_losses  fighter2_record_wins  \
0                    NaN                     NaN                   NaN   
1                    NaN                     NaN                   NaN   

   fighter2_record_draws  fighter2_record_losses  fighter1_height_cm  \
0                    NaN                     NaN                 NaN   
1                    NaN                     NaN                 NaN   

   fighter2_height_cm  fighter1_ko_percentage  fighter2_ko_percentage  
0                 NaN                     NaN                     NaN  
1                 NaN                     NaN                     NaN

In [1550]:
df_staged_cleaning['method_or_round'] = df_staged_cleaning['method_or_round'].str.split(' ')

In [1551]:
last_rounds = [new_list[2] for new_list in df_staged_cleaning['method_or_round']][:]
df_staged_cleaning['round'] = last_rounds

df_staged_cleaning.head()

fighter1_result   method_or_round  fighter1_record_wins  \
0          Winner  [RTD,, Round, 3]                   NaN   
1          Winner  [UD,, Round, 12]                   NaN   
2          Winner  [TKO,, Round, 2]                   NaN   
3          Winner  [UD,, Round, 12]                   NaN   
4          Winner  [TKO,, Round, 7]                   NaN   

   fighter1_record_draws  fighter1_record_losses  fighter2_record_wins  \
0                    NaN                     NaN                   NaN   
1                    NaN                     NaN                   NaN   
2                    NaN                     NaN                   NaN   
3                    NaN                     NaN                   NaN   
4                    NaN                     NaN                   NaN   

   fighter2_record_draws  fighter2_record_losses  fighter1_height_cm  \
0                    NaN                     NaN                 NaN   
1                    NaN                     NaN                 NaN   
2                    NaN                     NaN                 NaN   
3                    NaN                     NaN                 NaN   
4                    NaN                     NaN                 NaN   

   fighter2_height_cm  fighter1_ko_percentage  fighter2_ko_percentage round  
0                 NaN                     NaN                     NaN     3  
1                 NaN                     NaN                     NaN    12  
2                 NaN                     NaN                     NaN     2  
3                 NaN                     NaN                     NaN    12  
4                 NaN                     NaN                     NaN     7

In [1552]:
df_staged_cleaning = df_staged_cleaning.drop(columns='method_or_round')
df_staged_cleaning.head()

fighter1_result  fighter1_record_wins  fighter1_record_draws  \
0          Winner                   NaN                    NaN   
1          Winner                   NaN                    NaN   
2          Winner                   NaN                    NaN   
3          Winner                   NaN                    NaN   
4          Winner                   NaN                    NaN   

   fighter1_record_losses  fighter2_record_wins  fighter2_record_draws  \
0                     NaN                   NaN                    NaN   
1                     NaN                   NaN                    NaN   
2                     NaN                   NaN                    NaN   
3                     NaN                   NaN                    NaN   
4                     NaN                   NaN                    NaN   

   fighter2_record_losses  fighter1_height_cm  fighter2_height_cm  \
0                     NaN                 NaN                 NaN   
1                     NaN                 NaN                 NaN   
2                     NaN                 NaN                 NaN   
3                     NaN                 NaN                 NaN   
4                     NaN                 NaN                 NaN   

   fighter1_ko_percentage  fighter2_ko_percentage round  
0                     NaN                     NaN     3  
1                     NaN                     NaN    12  
2                     NaN                     NaN     2  
3                     NaN                     NaN    12  
4                     NaN                     NaN     7

### feature engineering swapped values + add to current values

In [1553]:

df_staged_swapping = df_staged_cleaning.copy()

fighter2_wins_temp = df_staged_swapping['fighter2_record_wins'].copy()
fighter2_draws_temp = df_staged_swapping['fighter2_record_draws'].copy()
fighter2_losses_temp = df_staged_swapping['fighter2_record_losses'].copy()
fighter2_height_cm_temp = df_staged_swapping['fighter2_height_cm'].copy()
fighter2_ko_percentage_temp = df_staged_swapping['fighter2_ko_percentage'].copy()

df_staged_swapping['fighter2_record_wins'] = df_staged_swapping['fighter1_record_wins']
df_staged_swapping['fighter2_record_draws'] = df_staged_swapping['fighter1_record_draws']
df_staged_swapping['fighter2_record_losses'] = df_staged_swapping['fighter1_record_losses']
df_staged_swapping['fighter2_height_cm'] = df_staged_swapping['fighter1_height_cm']
df_staged_swapping['fighter2_ko_percentage'] = df_staged_swapping['fighter1_ko_percentage']

df_staged_swapping['fighter1_record_wins'] = fighter2_wins_temp
df_staged_swapping['fighter1_record_draws'] = fighter2_draws_temp
df_staged_swapping['fighter1_record_losses'] = fighter2_losses_temp
df_staged_swapping['fighter1_height_cm'] = fighter2_height_cm_temp
df_staged_swapping['fighter1_ko_percentage'] = fighter2_ko_percentage_temp

def reverse_results(rowval) : 
    if rowval == 'Winner' :
        return 'Loser'
    elif rowval == 'Loser' :
        return 'Winner'
    else :
        return 'Draw'
    
df_staged_swapping['fighter1_result'] = df_staged_swapping['fighter1_result'].apply(reverse_results)


concatenate the matrices

In [1554]:
df_encoded = pd.concat([df_staged_cleaning, df_staged_swapping], axis=0)

In [1555]:
df_encoded

fighter1_result  fighter1_record_wins  fighter1_record_draws  \
0           Winner                   NaN                    NaN   
1           Winner                   NaN                    NaN   
2           Winner                   NaN                    NaN   
3           Winner                   NaN                    NaN   
4           Winner                   NaN                    NaN   
5             Draw                   NaN                    NaN   
6           Winner                   NaN                    NaN   
7           Winner                   NaN                    NaN   
8           Winner                   NaN                    NaN   
9           Winner                   NaN                    NaN   
10          Winner                   NaN                    NaN   
11          Winner                   NaN                    NaN   
0           Winner                  29.0                    0.0   
1           Winner                  62.0                    2.0   
2           Winner                   8.0                    1.0   
3            Loser                  24.0                    1.0   
4           Winner                  30.0                    3.0   
5           Winner                  39.0                    4.0   
6           Winner                  34.0                    3.0   
7           Winner                   8.0                    0.0   
8           Winner                  17.0                    0.0   
9           Winner                  15.0                    0.0   
10            Draw                  15.0                    0.0   
11          Winner                  35.0                    5.0   
0            Loser                   NaN                    NaN   
1            Loser                   NaN                    NaN   
2            Loser                   NaN                    NaN   
3            Loser                   NaN                    NaN   
4            Loser                   NaN                    NaN   
5             Draw                   NaN                    NaN   
6            Loser                   NaN                    NaN   
7            Loser                   NaN                    NaN   
8            Loser                   NaN                    NaN   
9            Loser                   NaN                    NaN   
10           Loser                   NaN                    NaN   
11           Loser                   NaN                    NaN   
0            Loser                  26.0                    1.0   
1            Loser                  23.0                    0.0   
2            Loser                  21.0                    2.0   
3           Winner                  16.0                    2.0   
4            Loser                  11.0                    7.0   
5            Loser                  15.0                    1.0   
6            Loser                  23.0                    0.0   
7            Loser                  23.0                    6.0   
8            Loser                  26.0                    2.0   
9            Loser                  19.0                    0.0   
10            Draw                  23.0                    6.0   
11           Loser                  22.0                    4.0   

    fighter1_record_losses  fighter2_record_wins  fighter2_record_draws  \
0                      NaN                   NaN                    NaN   
1                      NaN                   NaN                    NaN   
2                      NaN                   NaN                    NaN   
3                      NaN                   NaN                    NaN   
4                      NaN                   NaN                    NaN   
5                      NaN                   NaN                    NaN   
6                      NaN                   NaN                    NaN   
7                      NaN                   NaN                    NaN   
8                      NaN                  

could also feature engineer the ratio between fighters, such as fighter2/fighter1 for height

### encoding

In [1556]:
# commented out so that the concatenation of swapped fighters is correctly set
# df_encoded = df_staged_cleaning.copy()

In [1557]:
# WINNER = 0, LOSER = 1, DRAW = 2
def custom_encoder(value) :
    if value == 'Winner' :
        return 0
    elif value == 'Loser' :
        return 1
    else : return 2
df_encoded['fighter1_result'] = df_encoded['fighter1_result'].apply(custom_encoder)

In [1558]:
df_encoded.shape

(48, 12)

In [1559]:
df_encoded.info()

<class 'pandas.core.frame.DataFrame'>
Index: 48 entries, 0 to 11
Data columns (total 12 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   fighter1_result         48 non-null     int64  
 1   fighter1_record_wins    24 non-null     float64
 2   fighter1_record_draws   24 non-null     float64
 3   fighter1_record_losses  24 non-null     float64
 4   fighter2_record_wins    24 non-null     float64
 5   fighter2_record_draws   24 non-null     float64
 6   fighter2_record_losses  24 non-null     float64
 7   fighter1_height_cm      23 non-null     float64
 8   fighter2_height_cm      23 non-null     float64
 9   fighter1_ko_percentage  24 non-null     float64
 10  fighter2_ko_percentage  24 non-null     float64
 11  round                   48 non-null     object 
dtypes: float64(10), int64(1), object(1)
memory usage: 4.9+ KB


In [1560]:
df_encoded = df_encoded.infer_objects()
df_encoded['fighter1_record_wins'] = df_encoded['fighter1_record_wins'].astype('Int64')
df_encoded['fighter1_record_draws'] = df_encoded['fighter1_record_draws'].astype('Int64')
df_encoded['fighter1_record_losses'] = df_encoded['fighter1_record_losses'].astype('Int64')
df_encoded['fighter2_record_wins'] = df_encoded['fighter2_record_wins'].astype('Int64')
df_encoded['fighter2_record_draws'] = df_encoded['fighter2_record_draws'].astype('Int64')
df_encoded['fighter2_record_losses'] = df_encoded['fighter1_record_losses'].astype('Int64')
df_encoded['fighter2_height_cm'] = df_encoded['fighter2_height_cm'].astype('Int64')
df_encoded['fighter1_ko_percentage'] = df_encoded['fighter1_ko_percentage'].astype('Int64')
df_encoded['fighter2_ko_percentage'] = df_encoded['fighter2_ko_percentage'].astype('Int64')
df_encoded['round'] = df_encoded['round'].astype('Int64')

In [1561]:
df_encoded.info()

<class 'pandas.core.frame.DataFrame'>
Index: 48 entries, 0 to 11
Data columns (total 12 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   fighter1_result         48 non-null     int64  
 1   fighter1_record_wins    24 non-null     Int64  
 2   fighter1_record_draws   24 non-null     Int64  
 3   fighter1_record_losses  24 non-null     Int64  
 4   fighter2_record_wins    24 non-null     Int64  
 5   fighter2_record_draws   24 non-null     Int64  
 6   fighter2_record_losses  24 non-null     Int64  
 7   fighter1_height_cm      23 non-null     float64
 8   fighter2_height_cm      23 non-null     Int64  
 9   fighter1_ko_percentage  24 non-null     Int64  
 10  fighter2_ko_percentage  24 non-null     Int64  
 11  round                   48 non-null     Int64  
dtypes: Int64(10), float64(1), int64(1)
memory usage: 5.3 KB


In [1562]:
df_encoded.describe()

fighter1_result  fighter1_record_wins  fighter1_record_draws  \
count         48.00000                  24.0                   24.0   
mean           0.62500                  23.5               2.083333   
std            0.63998             11.481554               2.205067   
min            0.00000                   8.0                    0.0   
25%            0.00000                 15.75                    0.0   
50%            1.00000                  23.0                    1.5   
75%            1.00000                 26.75                   3.25   
max            2.00000                  62.0                    7.0   

       fighter1_record_losses  fighter2_record_wins  fighter2_record_draws  \
count                    24.0                  24.0                   24.0   
mean                 0.333333                  23.5               2.083333   
std                   0.56466             11.481554               2.205067   
min                       0.0                   8.0                    0.0   
25%                       0.0                 15.75                    0.0   
50%                       0.0                  23.0                    1.5   
75%                       1.0                 26.75                   3.25   
max                       2.0                  62.0                    7.0   

       fighter2_record_losses  fighter1_height_cm  fighter2_height_cm  \
count                    24.0           23.000000                23.0   
mean                 0.333333          174.913043          174.913043   
std                   0.56466            8.974272            8.974272   
min                       0.0          160.000000               160.0   
25%                       0.0          167.000000               167.0   
50%                       0.0          175.000000               175.0   
75%                       1.0          182.500000               182.5   
max                       2.0          191.000000               191.0   

       fighter1_ko_percentage  fighter2_ko_percentage     round  
count                    24.0                    24.0      48.0  
mean                   26.625                  26.625  7.833333  
std                 33.657886               33.657886  3.639811  
min                       0.0                     0.0       2.0  
25%                       0.0                     0.0      5.25  
50%                       0.0                     0.0       7.5  
75%                      59.5                    59.5      12.0  
max                      83.0                    83.0      12.0

### tt split

In [1563]:
from sklearn.model_selection import train_test_split

In [1564]:
X = df_encoded.drop(columns=['fighter1_result'])
y = df_encoded['fighter1_result']
y.unique()

array([0, 2, 1], dtype=int64)

In [1590]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.08, random_state=66) # tweak to maker sure that y values contain wins, losses, and draws. ts = .08 and rs =  66
print(y_test.unique())
print(y_train.unique())

[0 1 2]
[0 1 2]


## TRAIN MODEL - XGBoost First

In [1591]:
from xgboost import XGBClassifier

In [1592]:
xgbc = XGBClassifier(
    objective='multi:softmax',
    random_state=42,
    num_class=3,
    verbosity=1
)

In [1593]:
from sklearn.preprocessing import LabelEncoder
encoder = LabelEncoder()

In [1594]:
y_train = encoder.fit_transform(y_train)

In [1595]:
# compute sample weight based on class frequency
class_weights = dict(enumerate(len(y_train) / (len(np.unique(y_train)) * np.bincount(y_train))))
sample_weight = np.array([class_weights[label] for label in y_train])
sample_weight

array([0.73333333, 0.73333333, 0.73333333, 0.6984127 , 0.73333333,
       0.6984127 , 0.6984127 , 0.6984127 , 0.6984127 , 0.6984127 ,
       0.6984127 , 4.88888889, 0.6984127 , 0.73333333, 0.73333333,
       0.6984127 , 0.6984127 , 0.6984127 , 0.73333333, 0.73333333,
       0.6984127 , 0.73333333, 0.6984127 , 0.73333333, 0.73333333,
       0.6984127 , 0.73333333, 0.73333333, 0.6984127 , 0.6984127 ,
       0.6984127 , 0.73333333, 0.6984127 , 4.88888889, 0.6984127 ,
       0.73333333, 0.73333333, 4.88888889, 0.73333333, 0.73333333,
       0.6984127 , 0.6984127 , 0.73333333, 0.73333333])

In [1596]:
# # no class weighting
# xgbc.fit(X_train, y_train)

# class weighting
xgbc.fit(X_train, y_train, sample_weight=sample_weight)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              feature_weights=None, gamma=None, grow_policy=None,
              importance_type=None, interaction_constraints=None,
              learning_rate=None, max_bin=None, max_cat_threshold=None,
              max_cat_to_onehot=None, max_delta_step=None, max_depth=None,
              max_leaves=None, min_child_weight=None, missing=nan,
              monotone_constraints=None, multi_strategy=None, n_estimators=None,
              n_jobs=None, num_class=3, ...)

In [1597]:
xgbc_preds = xgbc.predict(X_test)
xgbc_preds = encoder.inverse_transform(xgbc_preds)

In [1598]:
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score

In [1599]:
print(accuracy_score(y_test, xgbc_preds))

0.75


In [1600]:
print(confusion_matrix(y_test, xgbc_preds))

[[1 1 0]
 [0 1 0]
 [0 0 1]]


In [1576]:
print(classification_report(y_test, xgbc_preds))

              precision    recall  f1-score   support

           0       0.38      0.50      0.43         6
           1       0.50      0.38      0.43         8
           2       1.00      1.00      1.00         1

    accuracy                           0.47        15
   macro avg       0.62      0.62      0.62        15
weighted avg       0.48      0.47      0.47        15



In [1577]:
xgbc_preds

array([1, 1, 0, 2, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 1], dtype=int64)

### grid search cross validated + XGBoost Classifier - same rseult as initial one

In [1578]:
from sklearn.model_selection import GridSearchCV

In [1579]:
eval_set = [(X, y)] # validation set for early stopping

In [1580]:
xgbc_model2 = XGBClassifier(
    objective='multi:softmax',
    random_state=42,
    num_class=3,
    verbosity=1,
    eval_metric="mlogloss"
)

In [1581]:
param_grid = {
    "subsample":[0.75, 1],
     "colsample_bytree":[0.75, 1],
     "max_depth":[2, 6, 10],
     "min_child_weight":[1, 2,3,4,5],
     "learning_rate":[1, 0.1, 0.01, .001],
}

In [1582]:
xgbc_grid = GridSearchCV(
    xgbc_model2,
    param_grid,
    cv=3,
    scoring="roc_auc"
)

In [1583]:
xgbc_grid.fit(X_train,y_train,eval_set=eval_set,verbose=1)

[0]	validation_0-mlogloss:0.95440
[1]	validation_0-mlogloss:0.92664
[2]	validation_0-mlogloss:0.87059
[3]	validation_0-mlogloss:0.86353
[4]	validation_0-mlogloss:0.85710
[5]	validation_0-mlogloss:0.88929
[6]	validation_0-mlogloss:0.89166
[7]	validation_0-mlogloss:0.82296
[8]	validation_0-mlogloss:0.78523
[9]	validation_0-mlogloss:0.77022
[10]	validation_0-mlogloss:0.76231
[11]	validation_0-mlogloss:0.82809
[12]	validation_0-mlogloss:0.81179
[13]	validation_0-mlogloss:0.79937
[14]	validation_0-mlogloss:0.80089
[15]	validation_0-mlogloss:0.80144
[16]	validation_0-mlogloss:0.79426
[17]	validation_0-mlogloss:0.80945
[18]	validation_0-mlogloss:0.79304
[19]	validation_0-mlogloss:0.79880
[20]	validation_0-mlogloss:0.80714
[21]	validation_0-mlogloss:0.80203
[22]	validation_0-mlogloss:0.82146
[23]	validation_0-mlogloss:0.86421
[24]	validation_0-mlogloss:0.86859
[25]	validation_0-mlogloss:0.81760
[26]	validation_0-mlogloss:0.83744
[27]	validation_0-mlogloss:0.82955
[28]	validation_0-mlogloss:0.8

c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 279, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true, **_kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 376, in _score
    return self._sign * self._score_func(y_true, y_pred, **scoring_kwargs)
                        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

[6]	validation_0-mlogloss:0.87651
[7]	validation_0-mlogloss:0.86211
[8]	validation_0-mlogloss:0.89133
[9]	validation_0-mlogloss:0.88753
[10]	validation_0-mlogloss:0.88016
[11]	validation_0-mlogloss:0.85111
[12]	validation_0-mlogloss:0.85651
[13]	validation_0-mlogloss:0.84572
[14]	validation_0-mlogloss:0.82094
[15]	validation_0-mlogloss:0.83014
[16]	validation_0-mlogloss:0.82722
[17]	validation_0-mlogloss:0.82412
[18]	validation_0-mlogloss:0.82201
[19]	validation_0-mlogloss:0.82328
[20]	validation_0-mlogloss:0.83407
[21]	validation_0-mlogloss:0.83114
[22]	validation_0-mlogloss:0.85259
[23]	validation_0-mlogloss:0.85145
[24]	validation_0-mlogloss:0.83714
[25]	validation_0-mlogloss:0.81587
[26]	validation_0-mlogloss:0.81783
[27]	validation_0-mlogloss:0.81724
[28]	validation_0-mlogloss:0.82858
[29]	validation_0-mlogloss:0.85577
[30]	validation_0-mlogloss:0.85976
[31]	validation_0-mlogloss:0.82057
[32]	validation_0-mlogloss:0.82091
[33]	validation_0-mlogloss:0.82867
[34]	validation_0-mloglo

c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 279, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true, **_kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 376, in _score
    return self._sign * self._score_func(y_true, y_pred, **scoring_kwargs)
                        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

[81]	validation_0-mlogloss:0.83826
[82]	validation_0-mlogloss:0.83798
[83]	validation_0-mlogloss:0.83780
[84]	validation_0-mlogloss:0.83766
[85]	validation_0-mlogloss:0.83754
[86]	validation_0-mlogloss:0.83861
[87]	validation_0-mlogloss:0.83772
[88]	validation_0-mlogloss:0.83672
[89]	validation_0-mlogloss:0.83804
[90]	validation_0-mlogloss:0.83754
[91]	validation_0-mlogloss:0.83851
[92]	validation_0-mlogloss:0.83917
[93]	validation_0-mlogloss:0.83757
[94]	validation_0-mlogloss:0.83713
[95]	validation_0-mlogloss:0.83807
[96]	validation_0-mlogloss:0.83718
[97]	validation_0-mlogloss:0.83684
[98]	validation_0-mlogloss:0.83776
[99]	validation_0-mlogloss:0.83653
[0]	validation_0-mlogloss:0.98807
[1]	validation_0-mlogloss:0.91007
[2]	validation_0-mlogloss:0.88360
[3]	validation_0-mlogloss:0.90407
[4]	validation_0-mlogloss:0.92314
[5]	validation_0-mlogloss:0.95946
[6]	validation_0-mlogloss:0.97593
[7]	validation_0-mlogloss:0.99092
[8]	validation_0-mlogloss:1.00288
[9]	validation_0-mlogloss:1.0

...

c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 279, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true, **_kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 376, in _score
    return self._sign * self._score_func(y_true, y_pred, **scoring_kwargs)
                        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

[1]	validation_0-mlogloss:1.09824
[2]	validation_0-mlogloss:1.09806
[3]	validation_0-mlogloss:1.09787
[4]	validation_0-mlogloss:1.09769
[5]	validation_0-mlogloss:1.09750
[6]	validation_0-mlogloss:1.09732
[7]	validation_0-mlogloss:1.09713
[8]	validation_0-mlogloss:1.09695
[9]	validation_0-mlogloss:1.09677
[10]	validation_0-mlogloss:1.09658
[11]	validation_0-mlogloss:1.09640
[12]	validation_0-mlogloss:1.09622
[13]	validation_0-mlogloss:1.09604
[14]	validation_0-mlogloss:1.09585
[15]	validation_0-mlogloss:1.09567
[16]	validation_0-mlogloss:1.09549
[17]	validation_0-mlogloss:1.09531
[18]	validation_0-mlogloss:1.09513
[19]	validation_0-mlogloss:1.09495
[20]	validation_0-mlogloss:1.09477
[21]	validation_0-mlogloss:1.09458
[22]	validation_0-mlogloss:1.09440
[23]	validation_0-mlogloss:1.09422
[24]	validation_0-mlogloss:1.09404
[25]	validation_0-mlogloss:1.09386
[26]	validation_0-mlogloss:1.09368
[27]	validation_0-mlogloss:1.09351
[28]	validation_0-mlogloss:1.09333
[29]	validation_0-mlogloss:1.

c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 279, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true, **_kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 376, in _score
    return self._sign * self._score_func(y_true, y_pred, **scoring_kwargs)
                        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^

[6]	validation_0-mlogloss:0.75505
[7]	validation_0-mlogloss:0.73728
[8]	validation_0-mlogloss:0.77575
[9]	validation_0-mlogloss:0.78838
[10]	validation_0-mlogloss:0.76213
[11]	validation_0-mlogloss:0.78531
[12]	validation_0-mlogloss:0.78537
[13]	validation_0-mlogloss:0.77738
[14]	validation_0-mlogloss:0.78067
[15]	validation_0-mlogloss:0.78388
[16]	validation_0-mlogloss:0.80171
[17]	validation_0-mlogloss:0.79975
[18]	validation_0-mlogloss:0.80503
[19]	validation_0-mlogloss:0.77658
[20]	validation_0-mlogloss:0.78081
[21]	validation_0-mlogloss:0.80102
[22]	validation_0-mlogloss:0.79467
[23]	validation_0-mlogloss:0.77382
[24]	validation_0-mlogloss:0.76076
[25]	validation_0-mlogloss:0.75324
[26]	validation_0-mlogloss:0.76776
[27]	validation_0-mlogloss:0.76725
[28]	validation_0-mlogloss:0.76363
[29]	validation_0-mlogloss:0.77757
[30]	validation_0-mlogloss:0.77739
[31]	validation_0-mlogloss:0.78236
[32]	validation_0-mlogloss:0.77990
[33]	validation_0-mlogloss:0.75417
[34]	validation_0-mloglo

GridSearchCV(cv=3,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None, device=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False,
                                     eval_metric='mlogloss', feature_types=None,
                                     feature_weights=None, gamma=None,
                                     grow_policy=None, importance_type=None,
                                     interaction_constrain...
                                     max_cat_to_onehot=None,
                                     max_delta_step=None, max_depth=None,
                                     max_leaves=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,
                                     multi_strategy=None, n_estimators=None,
                                     n_jobs=None, num_class=3, ...),
             param_grid={'colsample_bytree': [0.75, 1],
                         'learning_rate': [1, 0.1, 0.01, 0.001],
                         'max_depth': [2, 6, 10],
                         'min_child_weight': [1, 2, 3, 4, 5],
                         'subsample': [0.75, 1]},
             scoring='roc_auc')

In [1584]:
xgbc_grid.best_params_

{'colsample_bytree': 0.75,
 'learning_rate': 1,
 'max_depth': 2,
 'min_child_weight': 1,
 'subsample': 0.75}

In [1585]:
xgbc_cv_best = XGBClassifier(
    colsample_bytree = 0.75,
    learning_rate = 0.1,
    max_depth = 2,
    min_child_weight = 1,
    subsample = 0.75,
    objective='multi:softmax',
    random_state=42,
    num_class=3,
    verbosity=1,
    eval_metric="mlogloss"
)

In [1586]:
xgbc_cv_best.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.75, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric='mlogloss',
              feature_types=None, feature_weights=None, gamma=None,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=2, max_leaves=None,
              min_child_weight=1, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None, num_class=3, ...)

In [1587]:
xgbc_cv_best_preds = xgbc_cv_best.predict(X_test)
xgbc_cv_best_preds = encoder.inverse_transform(xgbc_cv_best_preds)

In [1588]:
confusion_matrix(y_test, xgbc_cv_best_preds)

array([[3, 3, 0],
       [5, 3, 0],
       [0, 1, 0]], dtype=int64)

In [1589]:
print(classification_report(y_test, xgbc_cv_best_preds))

              precision    recall  f1-score   support

           0       0.38      0.50      0.43         6
           1       0.43      0.38      0.40         8
           2       0.00      0.00      0.00         1

    accuracy                           0.40        15
   macro avg       0.27      0.29      0.28        15
weighted avg       0.38      0.40      0.38        15



c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Dylan\anaconda3\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
